In [4]:

import sqlalchemy as sa
from urllib.parse import quote_plus
import pandas as pd
import datetime as dt
# 
SERVER = "187.251.102.148"
PORT = 1433
DB = "CABANNA"
USER = "inventarios"
PWD = "Inventa#2017"


# Nombre del driver que acabas de instalar
driver = "ODBC Driver 18 for SQL Server"
driver_enc = quote_plus(driver)

# Connection string para SQLAlchemy + pyodbc
conn_str = (
    f"mssql+pyodbc://{USER}:{PWD}@{SERVER},{PORT}/{DB}"
    f"?driver={driver_enc}"
    "&TrustServerCertificate=yes"
)

engine = sa.create_engine(conn_str)


with engine.connect() as conn:
    result = conn.execute(sa.text("SELECT 1 AS test"))
    print(result.fetchall())



[(1,)]


In [18]:
# Ver qué tablas existen en la base

query_tablas = """
SELECT 
    TABLE_SCHEMA,
    TABLE_NAME
FROM INFORMATION_SCHEMA.TABLES
ORDER BY TABLE_SCHEMA, TABLE_NAME;
"""

df_tablas = pd.read_sql(query_tablas, engine)

# Lista única de tablas
tablas = df_tablas['TABLE_NAME'].unique().tolist()


# Lista única de tablas
tablas = df_tablas['TABLE_NAME'].unique().tolist()

tablas_con_datos = []

for i, tabla in enumerate(tablas):
    try:
        query = f"""
        SELECT TOP 100 *
        FROM dbo.[{tabla}]
        """
        
        df_tmp = pd.read_sql(query, engine)
        
        if not df_tmp.empty:
            tablas_con_datos.append({
                "index": i,
                "table_name": tabla,
                "rows_returned": len(df_tmp)
            })
        #     print(f"✅ [{i}] {tabla} → TIENE DATOS")
        # else:
        #     print(f"⚠️ [{i}] {tabla} → sin datos")
    
    except Exception as e:
        # Algunas tablas pueden fallar por permisos, vistas, etc.
        print(f"❌ [{i}] {tabla} → ERROR: {e}")


df_tablas_con_datos = pd.DataFrame(tablas_con_datos)
lista_tablas_con_datos = df_tablas_con_datos['table_name'].unique().tolist()

df_tablas.head()


TABLE_SCHEMA             TABLE_NAME
0          dbo    AA_AccionesCriticas
1          dbo  AA_ActivacionAditivas
2          dbo   AA_AlmacenesSucursal
3          dbo         AA_ArchivosXML
4          dbo          AA_Asistencia

In [16]:
# Ventas 
i_ventas = 640  

# Imprimir el indiced de la tabla y nombre de la tabla
tabla_seleccionada_ventas = tablas[i_ventas]
print(f"Tabla seleccionada (índice {i_ventas}): {tabla_seleccionada_ventas}")
# FROM dbo.[{tabla_seleccionada_ventas}]
# Hacer la consulta
query_ventas = f"""
SELECT TOP 5000 *
FROM dbo.RE_RemisionesLinea
WHERE Fecha >= '2025-12-20'
"""

# Guardar la consulta en un Dataframe
df_ventas = pd.read_sql(query_ventas, engine)
df_ventas = df_ventas[['Fecha','HoraCaptura','Folio', 'Estacion', 'Cod', 'Cant', 'PU', 'Desc','Mesero', 'Impto','ImptoAdic', 'Comision','MotivoDev','TipoCD', 'CodCombo','TipoDesc',]].copy()
df_ventas.head(20)


Tabla seleccionada (índice 640): RE_RemisionesLinea


Fecha         HoraCaptura    Folio  Estacion  Cod  Cant     PU  Desc  \
0  2025-12-20 2012-04-09 02:02:36   619942      2504    4   1.0   89.0   0.0   
1  2025-12-20 2012-04-09 01:55:07   619942      2504  213   1.0  826.0   0.0   
2  2025-12-20 2012-04-09 01:55:07   619942      2504  215   1.0  273.0   0.0   
3  2025-12-20 2012-04-09 02:02:58   619942      2504  305   1.0  179.0   0.0   
4  2025-12-20 2025-12-20 13:05:58   477537      2305  112   1.0   87.0   0.0   
5  2025-12-20 2025-12-20 13:16:59   477536      2305  300   1.0  319.0   0.0   
6  2025-12-20 2025-12-20 13:16:59   477536      2305  300   1.0  319.0   0.0   
7  2025-12-20 2025-12-20 12:05:17  1218878      2105  105   1.0   97.0   0.0   
8  2025-12-20 2025-12-20 12:05:17  1218878      2105  108   1.0   87.0   0.0   
9  2025-12-20 2025-12-20 11:43:29  1218877      2104  109   1.0   87.0   0.0   
10 2025-12-20 2025-12-20 13:05:58   477537      2305  109   1.0   93.0   0.0   
11 2025-12-20 2025-12-20 11:57:43  1218878      2105    4   1.0   82.0   0.0   
12 2025-12-20 2025-12-20 12:49:19   204865      6005   11   1.0  102.0   0.0   
13 2025-12-20 2025-12-20 12:55:06   477537      2305   14   2.0  105.0   0.0   
14 2025-12-20 2025-12-20 12:33:00  1218879      2101   14   1.0  103.0   0.0   
15 2025-12-20 2025-12-20 12:33:00  1218879      2101   14   1.0  103.0   0.0   
16 2025-12-20 2025-12-20 13:18:37   452045      2906   14   1.0  106.0   0.0   
17 2025-12-20 2025-12-20 13:18:37   452045      2906   13   1.0  115.0   0.0   
18 2025-12-20 2025-12-20 12:33:00  1218879      2101   15   1.0  120.0   0.0   
19 2025-12-20 2025-12-20 12:46:52   452038      2904  104   1.0   89.0   0.0   

    Mesero  Impto  ImptoAdic  Comision MotivoDev  TipoCD CodCombo  TipoDesc  
0    25010   1600          0       0.0                 0     None         0  
1    25010   1600          0       0.0                 0     None         0  
2    25010   1600          0       0.0                 0     None         0  
3    25010   1600          0       0.0                 0     None         0  
4    23021   1600          0       0.0                 0     None         0  
5    23040   1600          0       0.0                 0     None         0  
6    23040   1600          0       0.0                 0     None         0  
7    21061   1600          0       0.0                 0     None         0  
8    21061   1600          0       0.0                 0     None         0  
9    21036   1600          0       0.0                 0     None         0  
10   23021   1600          0       0.0                 0     None         0  
11   21061   1600          0       0.0                 0     None         0  
12   31043   1600          0       0.0                 0     None         0  
13   23021   1600          0       0.0                 0     None         0  
14   21036   1600          0       0.0                 0     None         0  
15   21036   1600          0       0.0                 0     None         0  
16   29009   1600          0       0.0                 0     None         0  
17   29009   1600          0       0.0                 0     None         0  
18   21036   1600          0       0.0                 0     None         0  
19   29022   1600          0       0.0                 0     None         0

In [15]:
df_ventas[df_ventas['TipoDesc']==1]

Fecha         HoraCaptura    Folio  Estacion   Cod  Cant     PU  \
891  2025-05-20 2025-05-20 12:29:19   191292      6003    13   1.0  112.0   
892  2025-05-20 2025-05-20 12:29:19   191292      6003   606   1.0  105.0   
916  2025-05-20 2025-05-20 11:25:32   331496      7104     3   1.0   35.0   
917  2025-05-20 2025-05-20 11:36:30   331496      7104     3   1.0   35.0   
918  2025-05-20 2025-05-20 11:05:28   331496      7104   105   2.0  103.0   
...         ...                 ...      ...       ...   ...   ...    ...   
4824 2025-05-20 2025-07-19 14:49:05  1015895      2202   921   1.0  174.0   
4825 2025-05-20 2025-07-19 15:22:07  1015895      2202   921   1.0  174.0   
4826 2025-05-20 2025-07-19 15:22:07  1015895      2202   921   1.0  174.0   
4827 2025-05-20 2025-05-20 15:17:37  1015895      2202  1078   1.0   21.0   
4828 2025-05-20 2025-07-19 16:21:59  1015895      2202  5151   1.0    0.0   

        Desc  Mesero  Impto  ImptoAdic  Comision MotivoDev  TipoCD CodCombo  \
891   4000.0   31001   1600          0       0.0                 0     None   
892   4000.0   31001   1600          0       0.0                 0     None   
916   2500.0   32010   1600          0       0.0                 0     None   
917   2500.0   32016   1600          0       0.0                 0     None   
918   2500.0   32010   1600          0       0.0                 0     None   
...      ...     ...    ...        ...       ...       ...     ...      ...   
4824  2500.0   22036   1600          0       0.0                 0     None   
4825  2500.0   22036   1600          0       0.0                 0     None   
4826  2500.0   22036   1600          0       0.0                 0     None   
4827  2500.0   22036   1600          0       0.0                 0     None   
4828  2500.0   22036   1600          0       0.0                 0     None   

      TipoDesc  
891          1  
892          1  
916          1  
917          1  
918          1  
...        ...  
4824         1  
4825         1  
4826         1  
4827         1  
4828         1  

[114 rows x 16 columns]

In [13]:
df_ventas['Desc'].value_counts()

Desc
0.0       4886
2500.0      57
1000.0      39
4000.0      18
Name: count, dtype: int64

In [ ]:
df_ventas['Impto'].value_counts()

In [ ]:
df_ventas['ImptoAdic'].value_counts()

In [ ]:
df_ventas['Comision'].value_counts()

In [ ]:
df_ventas['MotivoDev'].value_counts()

In [ ]:
df_ventas['TipoCD'].value_counts()

In [ ]:
df_ventas['CodCombo'].value_counts()

In [14]:
df_ventas['TipoDesc'].value_counts()

TipoDesc
0    4886
1     114
Name: count, dtype: int64

In [ ]:
df_ventas[df_ventas['Desc']==2500].iloc[:,0:30].columns

In [ ]:
# 1. Calcular el subtotal por línea (cantidad × precio unitario)
df_ventas['ventas_subtotal'] = df_ventas['Cant'] * df_ventas['PU']

# 2. Resumir el subtotal por Folio (total de la venta/remisión)
df_ventas_resumen = (
    df_ventas
    .groupby('Folio', as_index=False)['ventas_subtotal']
    .sum()
    .round(2)  # opcional: redondear a 2 decimales para moneda
)

# Mostrar resultado
df_ventas_resumen.head(20)

In [20]:
# Diccionario sucursal

i_sucursal=  6
# Nombre de la tabla seleccionada
tabla_seleccionada_sucursal= lista_tablas_con_datos[i_sucursal]
print(f"Tabla seleccionada (índice {i_sucursal}): {tabla_seleccionada_sucursal}")

query_sucursal= f"""
SELECT TOP 1000 *
FROM dbo.[{tabla_seleccionada_sucursal}];
"""

df_sucursal= pd.read_sql(query_sucursal, engine)
df_sucursal= df_sucursal[['Sucursal','NombreSucursal','Zona','Ciudad','Estado']].copy()
df_sucursal.head(20)

Tabla seleccionada (índice 6): AA_Sucursales


Sucursal        NombreSucursal      Zona            Ciudad Estado
0         10  CA-QRO ALIMENTOS (QR     BAJIO                         
1          3               POLANCO    CENTRO  CIUDAD DE MEXICO   CDMX
2          4     SFG ALIMENTOS SFE    CENTRO  CIUDAD DE MEXICO   CDMX
3          8  SFG ALIMENTOS TV AZT    CENTRO                         
4         11                PUEBLA    CENTRO            PUEBLA  PUEBL
5          5             AV MEXICO       GDL       GUADALAJARA    JAL
6          7           GOURMETERIA       GDL       GUADALAJARA    JAL
7         12             CD JUAREZ    JUAREZ        CD. JUAREZ   CHIH
8          6              MEXICALI  MEXICALI           MEXIALI     BC
9          9          METROPOLITAN     NORTE         MONTERREY   N.L.
10         1              CULIACAN  PACIFICO          CULIACAN    SIN
11       999          GRUPOCABANNA       SIN                         
12         2               TIJUANA   TIJUANA           TIJUANA     BC

In [ ]:
# Diccionario Menú 

i_munu =  621
# Nombre de la tabla seleccionada
tabla_seleccionada_menu = tablas[i_munu]
print(f"Tabla seleccionada (índice {i_munu}): {tabla_seleccionada_menu}")

query_menu = f"""
SELECT TOP 1000 *
FROM dbo.[{tabla_seleccionada_menu}];
"""

df_menu = pd.read_sql(query_menu, engine)
df_menu = df_menu[['Cod','Descripcion','Clasif','SubClasif']].copy()
df_menu.head()

In [ ]:
df_menu[df_menu['Cod']==13]

In [19]:
# Diccionario clasificación

i_menu_clasif =  535
# Nombre de la tabla seleccionada
tabla_seleccionada_menu_clasif = tablas[i_menu_clasif]
print(f"Tabla seleccionada (índice {i_menu_clasif}): {tabla_seleccionada_menu_clasif}")

query_menu_clasif = f"""
SELECT TOP 1000 *
FROM dbo.[{tabla_seleccionada_menu_clasif}];
"""

df_menu_clasif = pd.read_sql(query_menu_clasif, engine)
df_menu_clasif = df_menu_clasif[['Clasif','Descripcion']].copy()
df_menu_clasif

Tabla seleccionada (índice 535): RE_Clasificacion


Clasif             Descripcion
0     001              DESAYUNNOX
1      01                TOSTADAS
2      02          TACOS PLAYEROS
3      03            TACOS DE RES
4      04              AGUACHILES
5      05  TIRADITOS  Y ENSALADAS
6      06        ANTOJOS PLAYEROS
7      07         ANTOJOS CABANNA
8      08                  PIZZAS
9      09                INFANTIL
10     10                 POSTRES
11     11                    CAFE
12     12       AGUAS Y REFRESCOS
13     13             BAR COCKTEL
14     14             COCKTELERIA
15     15                 CERVEZA
16     16                   VINOS
17     17                   PROMO
18     18               VARIANTES
19     19          SERV DOMICILIO
20     20           CANALES VENTA
21     21             PLATAFORMAS
22     22                   ARCOS

In [ ]:
#Buscar una columna

# 2) Buscar cuáles de esas tablas contienen columna "Folio"
query_column = f"""
SELECT 
    TABLE_NAME,
    COLUMN_NAME
FROM INFORMATION_SCHEMA.COLUMNS
WHERE COLUMN_NAME = 'TipoDesc'
  AND TABLE_NAME IN ({",".join([f"'{t}'" for t in lista_tablas_con_datos])})
ORDER BY TABLE_NAME;
"""

df_column = pd.read_sql(query_column, engine)
 
for table_name in df_column["TABLE_NAME"].unique():
    i = lista_tablas_con_datos.index(table_name)
    print(f"✅ Tabla seleccionada tiene la columna Folio (índice {i}): {table_name}")

In [ ]:
# Busca indivual de tablas con la columna a buscar

i_column =  52
# Nombre de la tabla seleccionada
tabla_seleccionada_column = lista_tablas_con_datos[i_column]
print(f"Tabla seleccionada (índice {i_column}): {tabla_seleccionada_column}")

query_column = f"""
SELECT TOP 1000 *
FROM dbo.[{tabla_seleccionada_column}];
"""

df_column = pd.read_sql(query_column, engine)
# df_column = df_column[['subclasif','Descripcion']].copy()
df_column.head(20)

In [ ]:
df_column.columns

In [ ]:
df_ventas_enriquecido = (
    df_ventas
    # 1️⃣ Join ventas → columnas (para obtener Sucursal)
    .merge(
        df_column[['Estacion', 'Sucursal']],
        on='Estacion',
        how='left'
    )
    # 2️⃣ Join → sucursal (para traer metadatos)
    .merge(
        df_sucursal[['Sucursal', 'NombreSucursal', 'Zona', 'Ciudad', 'Estado']],
        on='Sucursal',
        how='left'
    )
)


In [ ]:
df_ventas_enriquecido

In [ ]:
df = df_ventas_enriquecido.copy()

# 1) Subtotal por línea (ajusta la fórmula si Desc es % o si ya tienes subtotal)
# df["ventas_subtotal_linea"] = (df["Cant"] * df["PU"]) - df["Desc"].fillna(0)

# 2) GroupBy por Folio conservando metadata + sumando subtotal
df_folio = (
    df.groupby("Folio", as_index=False)
      .agg(
          Fecha=("Fecha", "first"),
          HoraCaptura=("HoraCaptura", "first"),
          NombreSucursal=("NombreSucursal", "first"),
          Zona=("Zona", "first"),
          Ciudad=("Ciudad", "first"),
          Estado=("Estado", "first"),
          ventas_subtotal=("ventas_subtotal", "sum")
      )
)

df_folio


In [ ]:
df_folio['NombreSucursal'].unique()

In [ ]:

from dotenv import load_dotenv
load_dotenv()

from modules.drive import download_file_bytes,transformar_comensales_excel
import io

FILE_ID = "1qmJQ0Yi2hSIDzf0HeEoJtQA7Hw0NJm5P_bk0XTOlKh4"


content, meta = download_file_bytes(FILE_ID)

df_comensales = transformar_comensales_excel(io.BytesIO(content), year=2025)

df_comensales.head(50)



In [ ]:
from modules.drive import get_file_metadata
get_file_metadata("1qmJQ0Yi2hSIDzf0HeEoJtQA7Hw0NJm5P_bk0XTOlKh4")

---
---
---
---

In [ ]:
from modules.db import get_engine
import pandas as pd

def fetch_ventas_productos_por_sucursal(sucursal: str) -> pd.DataFrame:
    engine = get_engine()

    # 1) MIN / MAX de Fecha (FILTRADO por sucursal)
    query_minmax = """
        SELECT 
            MIN(v.Fecha) AS fecha_min,
            MAX(v.Fecha) AS fecha_max
        FROM dbo.RE_RemisionesLinea v
        LEFT JOIN dbo.AA_EstacionesSucursal es ON es.Estacion = v.Estacion
        LEFT JOIN dbo.AA_Sucursales s ON s.Sucursal = es.Sucursal
        WHERE LTRIM(RTRIM(s.NombreSucursal)) = LTRIM(RTRIM(?));
    """

    with engine.connect() as conn:
        df_minmax = pd.read_sql(query_minmax, conn, params=(sucursal,))

    if df_minmax.empty or pd.isna(df_minmax.loc[0, "fecha_min"]) or pd.isna(df_minmax.loc[0, "fecha_max"]):
        return pd.DataFrame()

    fecha_min = pd.to_datetime(df_minmax.loc[0, "fecha_min"])
    fecha_max = pd.to_datetime(df_minmax.loc[0, "fecha_max"])
    fin_exclusive = (fecha_max.normalize() + pd.Timedelta(days=1))  # ✅ incluye todo el día max

    query = """
        SELECT 
            v.Fecha,
            v.Folio,
            CAST(v.Cant AS DECIMAL(18,4)) AS Cant,
            CAST(v.PU   AS DECIMAL(18,4)) AS PU,

            p.Descripcion AS Platillo,
            p.Clasif      AS Clasif,
            c.Descripcion AS Clasificacion_Platillo,

            LTRIM(RTRIM(s.NombreSucursal)) AS NombreSucursal
        FROM dbo.RE_RemisionesLinea v
        LEFT JOIN dbo.RE_Platillos p ON p.Cod = v.Cod
        LEFT JOIN dbo.RE_Clasificacion c
            ON RIGHT('000' + LTRIM(RTRIM(p.Clasif)), 3) = RIGHT('000' + LTRIM(RTRIM(c.Clasif)), 3)
        LEFT JOIN dbo.AA_EstacionesSucursal es ON es.Estacion = v.Estacion
        LEFT JOIN dbo.AA_Sucursales s ON s.Sucursal = es.Sucursal
        WHERE v.Fecha >= ? AND v.Fecha < ?
          AND LTRIM(RTRIM(s.NombreSucursal)) = LTRIM(RTRIM(?))
        ORDER BY v.Fecha DESC, v.Folio DESC;
    """

    with engine.connect() as conn:
        df = pd.read_sql(query, conn, params=(fecha_min, fin_exclusive, sucursal))

    # Limpieza mínima
    df["Fecha"] = pd.to_datetime(df["Fecha"], errors="coerce")
    df["Cant"]  = pd.to_numeric(df["Cant"], errors="coerce").fillna(0.0)
    df["PU"]    = pd.to_numeric(df["PU"], errors="coerce").fillna(0.0)
    df["Ventas"] = df["Cant"] * df["PU"]

    df["Platillo"] = df["Platillo"].fillna("SIN_DESCRIPCION")
    df["Clasificacion_Platillo"] = df["Clasificacion_Platillo"].fillna("SIN_CLASIFICACION")

    df = df.dropna(subset=["Folio", "Fecha"])
    return df

sucursal = "AV MEXICO"

df = fetch_ventas_productos_por_sucursal(sucursal)


In [ ]:
df = df[~df['Clasificacion_Platillo'].isin(['PLATAFORMAS', 'ARCOS', 'PROMO', 'SERV DOMICILIO'])]
df

In [ ]:
# df[df['Platillo']=='2 REB AGUACATee']
df[df['Platillo']=='4 REB AGUACATE']

In [ ]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# Año
df["Year"] = df["Fecha"].dt.year.astype("int16")

# Limpieza strings (por si hay espacios raros)
df["Platillo"] = df["Platillo"].fillna("SIN_DESCRIPCION").astype(str).str.strip()
df["Folio"] = df["Folio"].astype(str).str.strip()

# Ingreso estimado: usa SOLO Cantidad positiva para evitar cancelaciones por devoluciones
df["Ingreso_Pos"] = np.where(df["Cant"] > 0, df["Cant"] * df["PU"], 0.0)

ticket_item = (
    df.groupby(["Year", "Folio", "Platillo"], as_index=False)
      .agg(
          cant_net=("Cant", "sum"),
          ingreso_pos=("Ingreso_Pos", "sum")
      )
)

ticket_item = ticket_item[ticket_item["cant_net"] > 0].copy()

tickets_year = (
    df.groupby("Year", as_index=False)
      .agg(tickets_total=("Folio", "nunique"))
)


inc_year_item = (
    ticket_item.groupby(["Year", "Platillo"], as_index=False)
              .agg(
                  tickets_con_producto=("Folio", "nunique"),
                  ingreso_estimado=("ingreso_pos", "sum")
              )
    .merge(tickets_year, on="Year", how="left")
)

inc_year_item["penetracion_ticket"] = inc_year_item["tickets_con_producto"] / inc_year_item["tickets_total"]


anchor_by_year = (
    inc_year_item.sort_values(["Year", "penetracion_ticket", "tickets_con_producto"], ascending=[True, False, False])
                .groupby("Year", as_index=False)
                .head(1)
                .rename(columns={"Platillo":"Producto_Ancla_Anio"})
)

anchor_by_year = anchor_by_year[[
    "Year",
    "Producto_Ancla_Anio",
    "tickets_total",
    "tickets_con_producto",
    "penetracion_ticket",
    "ingreso_estimado"
]].copy()



anio_actual = int(df["Year"].max())
producto_ancla_actual = anchor_by_year.loc[anchor_by_year["Year"] == anio_actual, "Producto_Ancla_Anio"].iloc[0]

anchor_actual_por_anio = (
    inc_year_item[inc_year_item["Platillo"] == producto_ancla_actual]
      .loc[:, ["Year", "penetracion_ticket", "tickets_con_producto", "ingreso_estimado"]]
      .rename(columns={
          "penetracion_ticket": "pen_ancla_actual",
          "tickets_con_producto": "tickets_ancla_actual",
          "ingreso_estimado": "ingreso_ancla_actual"
      })
)

# Unir para comparar por año: ancla_del_año vs ancla_actual
comp = (
    anchor_by_year.merge(anchor_actual_por_anio, on="Year", how="left")
)

comp["pen_ancla_actual"] = comp["pen_ancla_actual"].fillna(0.0)


In [ ]:
inc_year_item[inc_year_item['Year']== anio_actual].sort_values([ "penetracion_ticket", "tickets_con_producto"], ascending=[False, True]).head(5)

In [ ]:
comp[comp['Year'] == comp['Year'].max()]

In [ ]:
fig = go.Figure()

fig.add_trace(go.Bar(
    x=comp["Year"].astype(str),
    y=comp["penetracion_ticket"] * 100,
    name="Producto ancla de ese año",
    text=[f"{v*100:.1f}%" for v in comp["penetracion_ticket"]],
    textposition="outside",
    customdata=np.stack([
        comp["Producto_Ancla_Anio"],
        comp["tickets_con_producto"],
        comp["tickets_total"],
        comp["ingreso_estimado"]
    ], axis=1),
    hovertemplate=(
        "<b>Año %{x}</b><br>"
        "Ancla del año: <b>%{customdata[0]}</b><br>"
        "Penetración: <b>%{y:.1f}%</b><br>"
        "Tickets con ancla: %{customdata[1]} / %{customdata[2]}<br>"
        "Ingreso estimado: <b>$%{customdata[3]:,.0f}</b>"
        "<extra></extra>"
    )
))

fig.add_trace(go.Bar(
    x=comp["Year"].astype(str),
    y=comp["pen_ancla_actual"] * 100,
    name=f"Producto ancla del año actual ({producto_ancla_actual})",
    text=[f"{v*100:.1f}%" for v in comp["pen_ancla_actual"]],
    textposition="outside",
    customdata=np.stack([
        np.repeat(producto_ancla_actual, len(comp)),
        comp["tickets_ancla_actual"].fillna(0).astype(int),
        comp["tickets_total"],
        comp["ingreso_ancla_actual"].fillna(0.0)
    ], axis=1),
    hovertemplate=(
        "<b>Año %{x}</b><br>"
        "Ancla actual: <b>%{customdata[0]}</b><br>"
        "Penetración: <b>%{y:.1f}%</b><br>"
        "Tickets con ancla: %{customdata[1]} / %{customdata[2]}<br>"
        "Ingreso estimado: <b>$%{customdata[3]:,.0f}</b>"
        "<extra></extra>"
    )
))

fig.update_layout(
    title=(
        "Producto ancla por año — Penetración en ticket<br>"
        f"<sup>Comparación vs Ancla del año actual: <b>{producto_ancla_actual}</b> (año {anio_actual})</sup>"
    ),
    barmode="group",
    xaxis_title="Año",
    yaxis_title="Penetración en ticket (%)",
    height=520,
    margin=dict(l=10, r=10, t=80, b=70),
    legend=dict(orientation="h", yanchor="bottom", y=1.02, xanchor="right", x=1),
)

fig.show()


In [ ]:
import secrets
import string

def generar_api_key_segura(longitud=32):
    """
    Genera una API KEY criptográficamente segura.
    
    Args:
        longitud (int): Cantidad de bytes de entropía (32 bytes es estándar industrial = 256 bits).
    
    Returns:
        str: La API Key en formato URL-safe (seguro para enviar por HTTP).
    """
    # Opción 1: Estándar Industrial (Más robusto, mezcla letras, números y símbolos seguros)
    # Genera una cadena aleatoria codificada en Base64 modificado para URL.
    # 32 bytes de aleatoriedad se convierten en aprox 43 caracteres.
    api_key = secrets.token_urlsafe(longitud)
    
    return api_key

def generar_api_key_numerica_personalizada(longitud=32):
    """
    Genera una API KEY solo con letras y números (Alfanumérica), sin símbolos.
    Útil si tienes restricciones estrictas de caracteres.
    """
    # Definimos el alfabeto: Letras mayúsculas/minúsculas + Dígitos
    alfabeto = string.ascii_letters + string.digits
    
    # Usamos secrets.choice para elegir de forma segura
    api_key = ''.join(secrets.choice(alfabeto) for _ in range(longitud))
    
    return api_key

# --- EJECUCIÓN ---
print("--- Generador de Credenciales Seguras ---")

key_estandar = generar_api_key_segura()
print(f"🔐 API Key Estándar (Recomendada): {key_estandar}")

key_alfanumerica = generar_api_key_numerica_personalizada(40)
print(f"🔢 API Key Alfanumérica (Custom):  {key_alfanumerica}")